## A notebook to test different methods of the ECEF to WGS84 transformation

In [33]:
%pylab inline

import ICON
reload(ICON)
from pyglow import pyglow
import math


# Change matplotlib defaults
matplotlib.rcParams['savefig.dpi'] = 150
matplotlib.rcParams['figure.figsize'] = (4,3)
matplotlib.rcParams['font.size'] = 8
matplotlib.rcParams['savefig.bbox'] = 'tight'
matplotlib.rcParams['xtick.labelsize'] = 'small'
matplotlib.rcParams['ytick.labelsize'] = 'small'
matplotlib.rcParams['legend.fancybox'] = 'True'
matplotlib.rcParams['legend.fontsize'] = 'small'
matplotlib.rcParams['legend.numpoints'] = 1

Populating the interactive namespace from numpy and matplotlib


Iterative implementation taught by Paul Kintner.

In [89]:
def ecef_to_wgs84_iterative(ecef_xyz):
    lat_accuracy_thresh = 1e-14 # 1e-10 is roughly mm accuracy
    
    a,b,e = ICON.wgs84constants()

    x = 1.0*ecef_xyz[0]
    y = 1.0*ecef_xyz[1]
    z = 1.0*ecef_xyz[2]
   
    run = True

    # Compute longitude
    lon = np.arctan2(y,x)
    # Guess initial altitude
    alt = 0.0
    # Compute initial latitude
    p = np.sqrt(x**2 + y**2)
    lat = np.arctan(z/p / (1-e**2))

    maxiters = 1000
    numiters = 0
    while(run):
        # Estimate N from previous latitude
        N = a**2 / np.sqrt(a**2 * np.cos(lat)**2 + b**2 * np.sin(lat)**2)

        # Estimate altitude
        alt = p/np.cos(lat) - N

        # Estimate new latitude
        newlat = np.arctan(z/p / (1 - ((e**2*N)/(N+alt))))

        # Stop when necessary
        if abs(lat - newlat) < lat_accuracy_thresh:
            run = False

        # Check if we've reached maxiters
        if numiters > maxiters:
            raise Exception('maximum iterations reached')

        lat = newlat
        numiters += 1

    lat = lat * 180/np.pi
    lon = lon * 180/np.pi
    
    return np.array([lat, lon, alt])


According to the following blog post, this is the "best" closed-form implementation, from a paper by Olson.
https://possiblywrong.wordpress.com/2014/02/14/when-approximate-is-better-than-exact/

In [90]:
def ecef_to_wgs84_olson(ecef):
    # WGS-84 ellipsoid parameters
    a,b,_ = ICON.wgs84constants()
    f = 1-b/a

    # Derived parameters
    e2 = f * (2 - f)
    a1 = a * e2
    a2 = a1 * a1
    a3 = a1 * e2 / 2
    a4 = 2.5 * a2
    a5 = a1 + a3
    a6 = 1 - e2

    def ecef_to_lla(ecef):
        """Convert ECEF (meters) to LLA (radians and meters).
        """
        # Olson, D. K., Converting Earth-Centered, Earth-Fixed Coordinates to
        # Geodetic Coordinates, IEEE Transactions on Aerospace and Electronic
        # Systems, 32 (1996) 473-476.
        w = math.sqrt(ecef[0] * ecef[0] + ecef[1] * ecef[1])
        z = ecef[2]
        zp = abs(z)
        w2 = w * w
        r2 = z * z + w2
        r  = math.sqrt(r2)
        s2 = z * z / r2
        c2 = w2 / r2
        u = a2 / r
        v = a3 - a4 / r
        if c2 > 0.3:
            s = (zp / r) * (1 + c2 * (a1 + u + s2 * v) / r)
            lat = math.asin(s)
            ss = s * s
            c = math.sqrt(1 - ss)
        else:
            c = (w / r) * (1 - s2 * (a5 - u - c2 * v) / r)
            lat = math.acos(c)
            ss = 1 - c * c
            s = math.sqrt(ss)
        g = 1 - e2 * ss
        rg = a / math.sqrt(g)
        rf = a6 * rg
        u = w - rg * c
        v = zp - rf * s
        f = c * u + s * v
        m = c * v - s * u
        p = m / (rf / g + f)
        lat = lat + p
        if z < 0:
            lat = -lat

        lat = 180./np.pi * lat
        lon = 180./np.pi * math.atan2(ecef[1], ecef[0])
        alt = f + m * p / 2
        return np.array([lat, lon, alt])
    
    return ecef_to_lla(ecef)

This is the master function that can be called to use three different methods.

In [91]:
def ecef_to_wgs84(ecef_xyz, method='iterative'):
    '''
    Transform ecef to wgs84 coordinates, using one of the following methods:
    
    "iterative": The iterative approach taught by Paul Kintner
    "ublox"    : The simple closed-form solution in the PDF sent by Scott England and
                 presumably written by the people who make u-blox receivers.
                 (Current implementation for ICON)
    "olson"    : The complicated closed-from solution described in the following blog:
                 https://possiblywrong.wordpress.com/2014/02/14/when-approximate-is-better-than-exact/
    '''
    
    if method == 'iterative':
        return ecef_to_wgs84_iterative(ecef_xyz)
    
    elif method == 'ublox':
        return ICON.ecef_to_wgs84(ecef_xyz)
    
    elif method == 'olson':
        return ecef_to_wgs84_olson(ecef_xyz)
    
    else:
        raise Exception('"%s" not recognized' % method)

#### Test the difference between the three methods (for several different latitudes)

In [92]:
latv = [0, 10, 20, 30, 40, 50, 60, 70, 80, 90]
lonv = 20*ones_like(latv)
altv = 250*ones_like(latv)

In [93]:
err_iter  = zeros(len(latv))
err_ublox = zeros(len(latv))
err_olson = zeros(len(latv))

for i in range(len(latv)):
    lla_true = [latv[i], lonv[i], altv[i]]
    xyz_true = ICON.wgs84_to_ecef(lla_true)
    
    lla_iter = ecef_to_wgs84(xyz_true, 'iterative')
    xyz_iter = ICON.wgs84_to_ecef(lla_iter)
    err_iter[i] = norm(xyz_iter - xyz_true)*1e3
    
    lla_ublox = ecef_to_wgs84(xyz_true, 'ublox')
    xyz_ublox = ICON.wgs84_to_ecef(lla_ublox)  
    err_ublox[i] = norm(xyz_ublox - xyz_true)*1e3
    
    lla_olson = ecef_to_wgs84(xyz_true, 'olson')
    xyz_olson = ICON.wgs84_to_ecef(lla_olson)
    err_olson[i] = norm(xyz_olson - xyz_true)*1e3


In [94]:
# Replace zeros with a very small number so that it can be plotted on a log scale
err_iter[err_iter==0.0] = 1e-30
err_ublox[err_ublox==0.0] = 1e-30
err_olson[err_olson==0.0] = 1e-30

# Plot
semilogy(latv, err_iter, 'k.-', label='iterative')
semilogy(latv, err_ublox, 'r.-', label='ublox')
semilogy(latv, err_olson, 'g.-', label='olson')
xlabel('Latitude of test point [deg]')
ylabel('Error [m]')
legend(loc='best', framealpha=1)
grid()

It sure looks like the Olson implementation is the best. It even beats the iterative solution (presumably because the iterative solution has a finite tolerance. We could make the tolerance smaller, but then we press our luck that we run into machine precision, which we are very close to).

It's weird that the solution is perfect for all three methods at the pole, since the blog indicated that was where some methods have problems.